In [ ]:
import analytics.tranche_basket as bkt
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

from analytics.scenarios import run_tranche_scenarios, run_portfolio_scenarios, run_tranche_scenarios_rolldown
from analytics import Swaption, BlackSwaption, Index, BlackSwaptionVolSurface, Portfolio, ProbSurface
from db import dbengine
from datetime import date
from graphics import plot_time_color_map

dawnengine  = dbengine('dawndb')

value_date = (pd.datetime.today() - pd.offsets.BDay(2)).date()

In [ ]:
#Construct IG Swaption Portfolio
index = 'IG'
series = 30
option_delta = Index.from_name(index, series, '5yr')
option_delta.spread = 65
option1 = BlackSwaption(option_delta, date(2018, 10, 17), 60, option_type="payer")
option1.sigma = .398
option1.direction = 'Long'
option2 = BlackSwaption(option_delta, date(2018, 10, 17), 100, option_type="payer")
option2.sigma = .609
option2.direction = 'Short'
option1.notional = 100_000_000
option2.notional = 300_000_000
option_delta.notional = option1.notional * option1.delta + option2.notional * option2.delta

portf = Portfolio([option1, option2, option_delta])
portf.value_date = value_date
portf.reset_pv()

In [ ]:
#Run Swaption sensitivities
#Set Shock range
shock_min = -.3
shock_max = 1.25
spread_shock = np.arange(shock_min, shock_max, 0.05)
#Set Date range
earliest_expiry = min(portf.swaptions, key=lambda x: x.exercise_date).exercise_date
date_range = pd.bdate_range(value_date, earliest_expiry - pd.offsets.BDay(), freq='20B')
#date_range = [earliest_expiry - pd.offsets.BDay()]
#Setup Vol Surface
vs = BlackSwaptionVolSurface(index,series, value_date=value_date)
ps = ProbSurface(index,series, value_date=value_date)
vol_surface = vs[vs.list(option_type='payer')[-1]]
swaption_scens = run_portfolio_scenarios(portf, date_range, spread_shock, np.array([0]),
                                vol_surface, params=["pnl", "delta"])
#swaption delta is in protection terms: switch to risk terms
swaption_scens.delta = -swaption_scens.delta

In [ ]:
#Get current Tranche positions
sql_string = "select * from list_tranche_marks(%s)"
pos = pd.read_sql_query(sql_string, dawnengine, params=(value_date,), parse_dates=['maturity'])
tranche_port = []
for i, r in pos.iterrows():
    tranche_port.append(bkt.TrancheBasket(r.p_index, r.p_series, '5yr'))
    tranche_port[i].build_skew()
pos['basket'] = tranche_port
#Set Shock Range
spread_range = (1+ spread_shock) * option_delta.spread
#Run tranche scenarios
temp = []
for i, r in pos.iterrows():
    df = run_tranche_scenarios_rolldown(r.basket, spread_range, date_range, corr_map=False)
    temp.append(r.notional*df.xs(str(r.attach) + "-" + str(r.detach), axis=1, level=1))
tranches_scens = sum(temp)

In [ ]:
#Create snapshot of the the first scenario date
total_scens = swaption_scens.reset_index().merge(tranches_scens.reset_index(), 
                                   left_on=['date', 'spread'], 
                                   right_on=['date', 'spread_range'], 
                                   suffixes=['_s', '_t'])
total_scens['pnl'] = total_scens['pnl_s'] + total_scens['pnl_t']
total_scens['delta'] = total_scens['delta_s'] + total_scens['delta_t']
total_scens_single_date = total_scens.set_index('date').xs(date_range[0])
total_scens_single_date = total_scens_single_date.set_index('spread', drop=True)

In [ ]:
#tranche positions delta at different spreads
ax = total_scens_single_date.delta_t.plot(title = 'delta vs. spread levels')
ax.ticklabel_format(style='plain')
plt.tight_layout()

In [ ]:
#Tranche + Swaptions positions delta at different spreads
ax1 = total_scens_single_date.delta.plot()
ax1.ticklabel_format(style='plain')
plt.tight_layout()

In [ ]:
total_scens_single_date[['delta', 'delta_t', 'delta_s']].plot()

In [ ]:
total_scens_single_date[['pnl', 'pnl_t', 'pnl_s']].plot()

In [ ]:
total_scens.date = pd.to_datetime(total_scens.date)
total_scens = total_scens.set_index(['date'])
plot_time_color_map(total_scens, spread_range, attr="pnl")
#plot_time_color_map(df, shock_range, attr="final_delta", color_map= 'rainbow', centered = False)

In [ ]:
#PNL of just the swaptions
plot_time_color_map(swaption_scens, spread_range, attr="pnl")

In [ ]:
#Construct levered Super senior hedged with swaption
index = 'IG'
series = 30
option_delta = Index.from_name(index, series, '5yr')
option_delta.spread = 62
option_delta.notional = 1
option1 = BlackSwaption(option_delta, date(2018, 7, 19), 75, option_type="payer")
option1.sigma = .52
option1.direction = 'Long'
option1.notional = 2_000_000_000

#If we have two options instead of just one
option2 = BlackSwaption(option_delta, date(2018, 7, 19), 90, option_type="payer")
option2.sigma = .68
option2.direction = 'Long'
option2.notional = 6_000_000_000

option3 = BlackSwaption(option_delta, date(2018, 12, 19), 55, option_type="receiver")
option3.sigma = .373
option3.direction = 'Short'
option3.notional = 5_000_000_000

#portf = Portfolio([option1, option_delta])
portf = Portfolio([option1, option2, option3, option_delta])
portf.value_date = value_date
portf.reset_pv()
#Run Swaption sensitivities
#Set Shock range
shock_min = -.5
shock_max = 1.25
spread_shock = np.arange(shock_min, shock_max, 0.05)
#Set Date range
earliest_expiry = min(portf.swaptions, key=lambda x: x.exercise_date).exercise_date
date_range = pd.bdate_range(value_date, earliest_expiry - pd.offsets.BDay(), freq='10B')
#Setup Vol Surface
vs = BlackSwaptionVolSurface(index,series, value_date=value_date)
ps = ProbSurface(index,series, value_date=value_date)
vol_surface = vs[vs.list(option_type='payer')[-1]]
swaption_scens = run_portfolio_scenarios(portf, date_range, spread_shock, np.array([0]),
                                vol_surface, params=["pnl", "delta"])
#swaption delta is in protection terms: switch to risk terms
swaption_scens.delta = -swaption_scens.delta

notional = 30_000_000_000
t = bkt.TrancheBasket('IG', '29', '3yr')
t.build_skew()
#get back to 17bps, .36 delta
port_spread = 67
#t.rho = np.array([np.nan, 0.39691196, 0.48904597, 0.8, np.nan])
t.tweak(port_spread)
spread_range = (1+ spread_shock) * port_spread
tranches_scens = run_tranche_scenarios_rolldown(t, spread_range, date_range, corr_map=False)
tranches_scens = notional*tranches_scens.xs('15-100', axis=1, level=1)

In [ ]:
dawnengine.dispose()